In [1]:
import numpy as np
import pandas as pd

import tensorflow as tf
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras import Sequential
from tensorflow.keras.layers import Flatten, Dense, Dropout, Activation, Input, Bidirectional,SimpleRNN, Embedding, Conv1D, LSTM, MaxPooling1D, GlobalMaxPooling1D, Dropout
from tensorflow.keras.callbacks import EarlyStopping, ReduceLROnPlateau

from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, confusion_matrix, classification_report
from sklearn.preprocessing import OneHotEncoder
from sklearn.model_selection import train_test_split


from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_selection import chi2
from IPython.display import display
from sklearn.model_selection import train_test_split



from nltk.stem import PorterStemmer
import re
import nltk
nltk.download('stopwords')
nltk.download('punkt')
from nltk.corpus import stopwords

import matplotlib.pyplot as plt
import seaborn as sns

print(tf.__version__)


2024-07-15 08:30:51.782214: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: SSE4.1 SSE4.2 AVX AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
/home/hsibitenda/anaconda3/envs/harriet_env/lib/python3.11/site-packages/threadpoolctl.py:1214: RuntimeWarning: 
Found Intel OpenMP ('libiomp') and LLVM OpenMP ('libomp') loaded at
the same time. Both libraries are known to be incompatible and this
can cause random crashes or deadlocks on Linux when loaded in the
same Python program.
Using threadpoolctl may cause crashes or deadlocks. For more
information and possible workarounds, please see
    https://github.com/joblib/threadpoolctl/blob/master/multiple_openmp.md

  warnings.warn(msg, RuntimeWarning)
[nltk_data] Downloading package stopwords to
[nltk_data]     /home/hsibitenda/nltk_data...
[nltk_data]   Packag

2.12.0


In [2]:
# df_train.to_csv('/home/hsibitenda/scratch/harriet/sentiment_training2.csv')
# new_dataset.to_csv('/home/hsibitenda/scratch/harriet/sentiment_testing2.csv')

In [3]:
# df_train=pd.read_csv('/home/hsibitenda/scratch/harriet/sentiment_training.csv')
# df_train=df_train.astype(str)
# df_test2=pd.read_csv('/home/hsibitenda/scratch/harriet/sentiment_testing.csv')
# df_test2=df_test2.astype(str)

In [4]:
df_train=pd.read_csv('/home/hsibitenda/scratch/harriet/sentiment_training2.csv')
df_train=df_train.astype(str)
df_test2=pd.read_csv('/home/hsibitenda/scratch/harriet/sentiment_testing2.csv')
df_test2=df_test2.astype(str)

In [5]:
# df3=pd.concat([df_train,df_test2], axis=0)
# df3.shape
# # df=df_train.copy()

In [6]:
# df3.columns

In [7]:
# # Filter the DataFrame for rows where Common_Sentiment3 is "wrong"
# filtered_df = df[df['Common_Sentiment32'] != 'conflict']
# filtered_df.head(5)

In [8]:
# filtered_df.groupby('Common_Sentiment32')['Text_translate2'].count()

In [9]:
# df.groupby('Common_Sentiment32')['Text_translate2'].count()

In [10]:
# filtered_df['Sentiment2'] = filtered_df['Common_Sentiment32'].map({'negative':0,'neutral':1,'positive':2})

In [11]:
# df_train= filtered_df.copy()

In [12]:
# df_test2 = df[df['Common_Sentiment32'] == 'conflict']
df_test2.shape

(20132, 58)

In [13]:
df_train.shape

(1904, 58)

In [14]:
df=df_train.copy()

In [15]:
df.columns

Index(['Unnamed: 0.5', 'Unnamed: 0.4', 'Unnamed: 0.3', 'Unnamed: 0.2',
       'Unnamed: 0', 'textid', 'Date', 'Views', 'sourcetype', 'alltext',
       'Text_emt', 'Text_emj', 'Text_langue', 'Text_translate', 'Text_langue2',
       'Text_lower', 'Text_punct', 'Text_tags', 'Text_chat', 'Text_spell',
       'Text_langue3', 'Text_translate2', 'Text_token', 'Text_stop',
       'Text_stem', 'Text_lemma', 'berttopic2', 'cluster_id2',
       'llama2_labelone10', 'cluster_labelone10', 'cluster_id',
       'llama2_labelone', 'cluster_labelone', 'Unnamed: 0.1', 'Text_lemma2',
       'Bertscore_Labels', 'Final_Labels', 'Predicted_Categories3', 'polarity',
       'subjectivity', 'Textblob', 'VADER', 'neg', 'neu', 'pos', 'compound',
       'BERT', 'Sentiment_Score', 'Sentiwordnet', 'llama3_sentiment',
       'Emotion', 'Emotional_Polarity', 'Common_Sentiment32', 'Sentiment2',
       'Predicted_Labels', 'Sentiment2_prediction', 'Sentiment2_roberta',
       'Predicted_Labels_roberta'],
      dtype='ob

In [17]:
import numpy as np
import pandas as pd
import os
from tqdm import tqdm
import bitsandbytes as bnb
import torch
import torch.nn as nn
import transformers
from torch import cuda
from datasets import Dataset
from peft import LoraConfig, PeftConfig
# from peft import get_peft_model
from trl import SFTTrainer
from trl import setup_chat_format
from transformers import (AutoModelForCausalLM, 
                          AutoTokenizer, 
                          BitsAndBytesConfig, 
                          TrainingArguments, 
                          pipeline, 
                          logging)
from sklearn.metrics import (accuracy_score, 
                             classification_report, 
                             confusion_matrix)
from sklearn.model_selection import train_test_split
from sentence_transformers import SentenceTransformer
from datasets import Dataset

In [ ]:
import os
import subprocess
import getpass
from huggingface_hub import notebook_login

# Define the path to the token file
token_file_path = "../your_token.txt"  # Replace with the actual path

if os.path.exists(token_file_path):
    # If the token file exists, read the token from the file
    with open(token_file_path, "r") as file:
        token = file.read().strip()
else:
    # If the token file does not exist, prompt the user to enter the token securely
    print("Please enter your ..:")
    token = getpass.getpass()

# Set up the environment variable with the token
os.environ["HUGGINGFACE_TOKEN"] = token

# Use transformers-cli to login
command = f'transformers-cli login --token {token}'
subprocess.run(command, shell=True)

In [18]:
from torch import bfloat16
import transformers

# set quantization configuration to load large model with less GPU memory
# this requires the `bitsandbytes` library

bnb_config = transformers.BitsAndBytesConfig(
    load_in_4bit=True,  # 4-bit quantization
    bnb_4bit_quant_type='nf4',  # Normalized float 4
    bnb_4bit_use_double_quant=True,  # Second quantization after the first
    bnb_4bit_compute_dtype=bfloat16  # Computation type
)
torch.backends.cuda.enable_mem_efficient_sdp(False)
torch.backends.cuda.enable_flash_sdp(False)

In [19]:
df.shape

(1904, 58)

In [20]:
# Set the device
device = f'cuda:{cuda.current_device()}' if cuda.is_available() else 'cpu'

# Define the model ID
model_id = "meta-llama/Meta-Llama-3-8B"

# Llama 2 Tokenizer
tokenizer = AutoTokenizer.from_pretrained(model_id, max_length=128)
tokenizer.pad_token = tokenizer.eos_token

# Load Llama 2 Model
model = AutoModelForCausalLM.from_pretrained(
    model_id,
    trust_remote_code=True,
    quantization_config=None  # No quantization config provided
)

# Set device
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model.to(device)
model.eval()

# Our text generator
generator = transformers.pipeline(
    model=model, tokenizer=tokenizer,
    task='text-generation',
    temperature=0.1,
    max_new_tokens=500,
    repetition_penalty=1.1,
    device=device  # Specify the device here
)



Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

In [21]:
# # Pre-calculate embeddings
# df.reset_index(drop=True, inplace=True)

# embedding_model = SentenceTransformer("BAAI/bge-small-en")
# embeddings = embedding_model.encode(df['Text_translate2'], show_progress_bar=True)


In [22]:
# Function to evaluate model predictions
def evaluate(y_true, y_pred):
    labels = ['positive', 'neutral', 'negative']
    mapping = {'positive': 2, 'neutral': 1, 'negative': 0}
    def map_func(x):
        return mapping.get(x, 1)
    
    y_true = np.vectorize(map_func)(y_true)
    y_pred = np.vectorize(map_func)(y_pred)
    
    # Calculate accuracy
    accuracy = accuracy_score(y_true=y_true, y_pred=y_pred)
    print(f'Accuracy: {accuracy:.3f}')
    
    # Generate accuracy report
    unique_labels = set(y_true)  # Get unique labels
    
    for label in unique_labels:
        label_indices = [i for i in range(len(y_true)) 
                         if y_true[i] == label]
        label_y_true = [y_true[i] for i in label_indices]
        label_y_pred = [y_pred[i] for i in label_indices]
        accuracy = accuracy_score(label_y_true, label_y_pred)
        print(f'Accuracy for label {label}: {accuracy:.3f}')
        
    # Generate classification report
    class_report = classification_report(y_true=y_true, y_pred=y_pred)
    print('\nClassification Report:')
    print(class_report)
    
    # Generate confusion matrix
    conf_matrix = confusion_matrix(y_true=y_true, y_pred=y_pred, labels=[0, 1, 2])
    print('\nConfusion Matrix:')
    print(conf_matrix)
    

In [23]:
from transformers import AutoTokenizer, AutoModelForCausalLM, TextGenerationPipeline
from imblearn.under_sampling import RandomUnderSampler

def predict(test, model, tokenizer, generator, device, max_length=128):
    y_preds = []
    for i in range(len(test)):
        prompt = test.iloc[i]["Text_translate2"]
        prompt = prompt[:max_length]
        prompt_tensor = torch.tensor([tokenizer.encode(prompt)], device=device)  # Convert prompt to tensor
        prompt_text = tokenizer.decode(prompt_tensor[0], skip_special_tokens=True)  # Convert tensor to string
        # Ensure that input_ids tensor is placed on the same device as the model
        input_ids = prompt_tensor.to(device)
        result = generator(text_inputs=prompt_text, max_length=128, num_return_sequences=1)  # Remove input_ids
        answer = result[0]['generated_text'].split("=")[-1].strip()
        if "positive" in answer:
            y_preds.append("positive")
        elif "neutral" in answer:
            y_preds.append("neutral")
        elif "negative" in answer:
            y_preds.append("negative")
        else:
            # Handle unexpected cases
            y_preds.append("neutral")
    return y_preds
# Undersample majority class using RandomUnderSampler
rus = RandomUnderSampler(random_state=42)
balanced_data, balanced_labels = rus.fit_resample(df[['Text_translate2']], df['Common_Sentiment32'])
# Convert balanced_data and balanced_labels to DataFrames for convenience
balanced_df = pd.DataFrame(balanced_data, columns=['Text_translate2'])
balanced_df['Common_Sentiment32'] = balanced_labels



# Split data into train, test, and evaluation sets
X_train = list()
X_test = list()

for sentiment in ["positive", "neutral", "negative"]:
    sentiment_data = balanced_df[balanced_df.Common_Sentiment32 == sentiment]
    train, test = train_test_split(sentiment_data, 
                                   train_size=0.8, 
                                   test_size=0.2, 
                                   stratify=sentiment_data['Common_Sentiment32'],
                                   random_state=42)
    X_train.append(train)
    X_test.append(test)


X_train = pd.concat(X_train).sample(frac=1, random_state=10)
X_test = pd.concat(X_test)

# Select evaluation samples
eval_idx = [idx for idx in df.index if idx not in list(train.index) + list(test.index)]
X_eval = df[df.index.isin(eval_idx)]
X_eval = (X_eval
          .groupby('Common_Sentiment32', group_keys=False)
          .apply(lambda x: x.sample(n=50, random_state=10, replace=True)))
X_train = X_train.reset_index(drop=True)

# Generate prompts for train and evaluation sets
def generate_prompt(data_point):
    return f"""
            Analyze the sentiment of the news headline enclosed in square brackets, 
            determine if it is positive, neutral, or negative, and return the answer as 
            the corresponding sentiment label "positive" or "neutral" or "negative".

            [{data_point["Text_translate2"]}] = {data_point["Common_Sentiment32"]}
            """.strip()

def generate_test_prompt(data_point):
    return f"""
            Analyze the sentiment of the news headline enclosed in square brackets, 
            determine if it is positive, neutral, or negative, and return the answer as 
            the corresponding sentiment label "positive" or "neutral" or "negative".

            [{data_point["Text_translate2"]}] = """.strip()

X_train = pd.DataFrame(X_train.apply(generate_prompt, axis=1), 
                       columns=["Text_translate2"])
X_eval = pd.DataFrame(X_eval.apply(generate_prompt, axis=1), 
                      columns=["Text_translate2"])

# Get true labels for evaluation
y_true = X_test.Common_Sentiment32


# Generate prompts for the test set
X_test = pd.DataFrame(X_test.apply(generate_test_prompt, axis=1), columns=["Text_translate2"])

train_data = Dataset.from_pandas(X_train)
eval_data = Dataset.from_pandas(X_eval)
# Generate predictions for the test set
y_pred = predict(X_test, model, tokenizer, generator, device)
# y_preds = predict(test=X_test, model=model, tokenizer=tokenizer, generator=generator, device=device)#, max_input_length=max_input_length)

# Calculate accuracy
accuracy = accuracy_score(y_true=y_true, y_pred=y_pred)
print(f'Accuracy: {accuracy:.3f}')


Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Both `max_new_tokens` (=500) and `max_length`(=128) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Both `max_new_tokens` (=500) and `max_length`(=128) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Both `max_new_tokens` (=500) and `max_length`(=128) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Setting `pad_token_id` to `eos_

Accuracy: 0.356


In [24]:
# Convert text prompts to numerical data
X_train_tensor = torch.tensor(range(len(X_train)), device=device)
X_eval_tensor = torch.tensor(range(len(X_eval)), device=device)

# Define output directory for training weights
output_dir="trained_weights2"
peft_config = LoraConfig(
    lora_alpha=16, 
    lora_dropout=0.1,
    r=64,
    bias="none",
    target_modules="lm_head",  # Specify lm_head as the target module
    # target_modules=["q_proj", "k_proj", "v_proj", "o_proj",
    #                 "gate_proj", "up_proj", "down_proj",],
    task_type="CAUSAL_LM",
)

training_arguments = TrainingArguments(
    output_dir=output_dir,                    # directory to save and repository id
    num_train_epochs=3,                       # number of training epochs
    per_device_train_batch_size=1,            # batch size per device during training
    gradient_accumulation_steps=8,            # number of steps before performing a backward/update pass
    gradient_checkpointing=True,              # use gradient checkpointing to save memory
    optim="paged_adamw_32bit",
    save_steps=0,
    logging_steps=25,                         # log every 10 steps
    learning_rate=2e-4,                       # learning rate, based on QLoRA paper
    weight_decay=0.001,
    fp16=True,
    bf16=False,
    max_grad_norm=0.3,                        # max gradient norm based on QLoRA paper
    max_steps=-1,
    warmup_ratio=0.03,                        # warmup ratio based on QLoRA paper
    group_by_length=True,
    lr_scheduler_type="cosine",               # use cosine learning rate scheduler
    report_to="tensorboard",                  # report metrics to tensorboard
    evaluation_strategy="epoch"               # save checkpoint every epoch
)

trainer = SFTTrainer(
    model=model,
    args=training_arguments,
    train_dataset=train_data,  # Assuming train_data is defined elsewhere
    eval_dataset=eval_data,    # Assuming eval_data is defined elsewhere
    peft_config=peft_config,   # Assuming peft_config is defined elsewhere
    dataset_text_field="Text_translate2",
    tokenizer=tokenizer,
    max_seq_length=1024,
    packing=False,
    dataset_kwargs={
        "add_special_tokens": False,
        "append_concat_token": False,
    }
)
trainer.train()


Map:   0%|          | 0/174 [00:00<?, ? examples/s]

Map:   0%|          | 0/150 [00:00<?, ? examples/s]

You're using a PreTrainedTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.
`use_cache=True` is incompatible with gradient checkpointing. Setting `use_cache=False`...
/home/hsibitenda/anaconda3/envs/harriet_env/lib/python3.11/site-packages/torch/utils/checkpoint.py:429: UserWarning: torch.utils.checkpoint: please pass in use_reentrant=True or use_reentrant=False explicitly. The default value of use_reentrant will be updated to be False in the future. To maintain current behavior, pass use_reentrant=True. It is recommended that you use use_reentrant=False. Refer to docs for more details on the differences between the two variants.
  warnings.warn(


TrainOutput(global_step=63, training_loss=3.044631836906312, metrics={'train_runtime': 80.6475, 'train_samples_per_second': 6.473, 'train_steps_per_second': 0.781, 'total_flos': 1949996536627200.0, 'train_loss': 3.044631836906312, 'epoch': 2.9})

In [25]:
# df1=df_test2.copy()
# df1.shape

In [26]:
# # # y_pred
# # Select relevant columns from df
# X_test = df1[['Text_translate2', 'Common_Sentiment32']]

# # Apply generate_test_prompt function
# X_test = pd.DataFrame(X_test.apply(generate_test_prompt, axis=1), columns=["Text_translate2"])

# # Generate predictions for the test set
# # y_pred = predict(X_test, model, tokenizer)

# # Call the predict function with all required arguments
# # y_pred = predict(X_test, model, tokenizer, generator, device)
# y_pred = predict(X_test, model, tokenizer, generator, device)#max_input_length)

# # Extract true labels from df
# y_true = df1['Common_Sentiment32']
# # Add predicted values as a new column in the DataFrame
# df1['Predicted_Sentiment_finetunned'] = y_pred

In [27]:
# df1.to_csv('/home/hsibitenda/scratch/harriet/sentiments_llama2_sent_new1.csv')

In [28]:
# df1

In [29]:
# import pandas as pd

# # Reset the index of each dataframe before concatenation
# df1_reset = df1.reset_index(drop=True)
# df2_reset = df2.reset_index(drop=True)
# df3_reset = df3.reset_index(drop=True)
# df4_reset = df4.reset_index(drop=True)

# # Concatenate the dataframes
# df7 = pd.concat([df1_reset, df2_reset, df3_reset, df4_reset], axis=0)

# # Print the shape of the concatenated dataframe
# print(df7.shape)
# df7.to_csv('/home/hsibitenda/scratch/harriet/sentiments_llama2_sentall2.csv')

### Finetunning

In [30]:




# y_preds = predict(test, model, tokenizer, generator, device)
# # y_preds = predict(test=X_test, model=model, tokenizer=tokenizer, generator=generator, device=device, max_input_length=max_input_length)

# evaluate(y_true, y_preds)

In [31]:
# df.head()
# evaluate(y_true, y_preds)

In [32]:
# Save trained model and tokenizer
trainer.save_model()
tokenizer.save_pretrained(output_dir)

/home/hsibitenda/anaconda3/envs/harriet_env/lib/python3.11/site-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")


('trained_weights2/tokenizer_config.json',
 'trained_weights2/special_tokens_map.json',
 'trained_weights2/tokenizer.json')

In [33]:
%reload_ext tensorboard
%tensorboard --logdir logs/runs

Reusing TensorBoard on port 6006 (pid 1443182), started 15 days, 20:22:50 ago. (Use '!kill 1443182' to kill it.)

In [34]:
df.columns

Index(['Unnamed: 0.5', 'Unnamed: 0.4', 'Unnamed: 0.3', 'Unnamed: 0.2',
       'Unnamed: 0', 'textid', 'Date', 'Views', 'sourcetype', 'alltext',
       'Text_emt', 'Text_emj', 'Text_langue', 'Text_translate', 'Text_langue2',
       'Text_lower', 'Text_punct', 'Text_tags', 'Text_chat', 'Text_spell',
       'Text_langue3', 'Text_translate2', 'Text_token', 'Text_stop',
       'Text_stem', 'Text_lemma', 'berttopic2', 'cluster_id2',
       'llama2_labelone10', 'cluster_labelone10', 'cluster_id',
       'llama2_labelone', 'cluster_labelone', 'Unnamed: 0.1', 'Text_lemma2',
       'Bertscore_Labels', 'Final_Labels', 'Predicted_Categories3', 'polarity',
       'subjectivity', 'Textblob', 'VADER', 'neg', 'neu', 'pos', 'compound',
       'BERT', 'Sentiment_Score', 'Sentiwordnet', 'llama3_sentiment',
       'Emotion', 'Emotional_Polarity', 'Common_Sentiment32', 'Sentiment2',
       'Predicted_Labels', 'Sentiment2_prediction', 'Sentiment2_roberta',
       'Predicted_Labels_roberta'],
      dtype='ob

In [35]:
import gc

del [model, tokenizer, peft_config, trainer, train_data, eval_data, bnb_config, training_arguments]
del [df, X_train, X_eval]
del [TrainingArguments, SFTTrainer, LoraConfig, BitsAndBytesConfig]

In [36]:
for _ in range(100):
    torch.cuda.empty_cache()
    gc.collect()

In [41]:
from peft import AutoPeftModelForCausalLM

finetuned_model = "/home/hsibitenda/scratch/harriet/sentiments/trained_weights2"
compute_dtype = getattr(torch, "float16")
tokenizer = AutoTokenizer.from_pretrained("meta-llama/Meta-Llama-3-8B")

model = AutoPeftModelForCausalLM.from_pretrained(
     finetuned_model,
     torch_dtype=compute_dtype,
     return_dict=False,
     low_cpu_mem_usage=True,
     device_map=device,
)

merged_model = model.merge_and_unload()
merged_model.save_pretrained("./merged_model2",safe_serialization=True, max_shard_size="2GB")
tokenizer.save_pretrained("./merged_model2")

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


('./merged_model2/tokenizer_config.json',
 './merged_model2/special_tokens_map.json',
 './merged_model2/tokenizer.json')

In [42]:
# y_pred = predict(X_test, merged_model, tokenizer, generator, device)
max_input_length = 128
y_preds = predict(test=X_test, model=model, tokenizer=tokenizer, generator=generator, device=device)#, max_input_length=max_input_length)



/home/hsibitenda/anaconda3/envs/harriet_env/lib/python3.11/site-packages/transformers/pipelines/base.py:1101: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Both `max_new_tokens` (=500) and `max_length`(=128) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Both `max_new_tokens` (=500) and `max_length`(=128) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Both `max_new_tokens` (=500) and

In [43]:
X_test.shape

(45, 1)

In [44]:
evaluate(y_true, y_preds)

Accuracy: 0.333
Accuracy for label 0: 0.333
Accuracy for label 1: 0.600
Accuracy for label 2: 0.067

Classification Report:
              precision    recall  f1-score   support

           0       0.26      0.33      0.29        15
           1       0.39      0.60      0.47        15
           2       0.33      0.07      0.11        15

    accuracy                           0.33        45
   macro avg       0.33      0.33      0.29        45
weighted avg       0.33      0.33      0.29        45


Confusion Matrix:
[[5 9 1]
 [5 9 1]
 [9 5 1]]


In [35]:
# y_pred = predict(test, model, tokenizer)
# evaluate(y_true, y_preds)

Accuracy: 0.817
Accuracy for label 0: 0.000
Accuracy for label 1: 0.000
Accuracy for label 2: 0.994

Classification Report:
              precision    recall  f1-score   support

           0       0.00      0.00      0.00        53
           1       0.00      0.00      0.00        15
           2       0.82      0.99      0.90       314

    accuracy                           0.82       382
   macro avg       0.27      0.33      0.30       382
weighted avg       0.67      0.82      0.74       382


Confusion Matrix:
[[  0   0  53]
 [  0   0  15]
 [  1   1 312]]


In [ ]:
# y_pred = predict(test, model, tokenizer)
# evaluate(y_true, y_preds)

In [ ]:
# y_pred = predict(test, model, tokenizer)
# evaluate(y_true, y_preds)

In [ ]:
# df=df_train.copy()
# df.columns

In [43]:
# # # y_pred
# # Select relevant columns from df
# X_test = df[['Text_translate2', 'Common_Sentiment32']]

# # Apply generate_test_prompt function
# X_test = pd.DataFrame(X_test.apply(generate_test_prompt, axis=1), columns=["Text_translate2"])

# # Generate predictions for the test set
# # y_pred = predict(X_test, model, tokenizer)

# # Call the predict function with all required arguments
# y_pred = predict(X_test, merged_model, tokenizer, generator, device)#,max_input_length)

# # Extract true labels from df
# y_true = df['Common_Sentiment32']
# # Add predicted values as a new column in the DataFrame
# df['Predicted_Sentiment_finetunned'] = y_pred

In [44]:
# df.to_csv('/home/hsibitenda/scratch/harriet/sentiments/sents_finetune_train.csv')

In [125]:
# df1=pd.read_csv('/home/hsibitenda/scratch/harriet/sentiments/batch21_1.csv')
# df1=df1.astype(str)

In [ ]:
df13=df_test2.copy()
# Calculate the number of batches needed
num_batches = len(df13) // 10000 + (len(df13) % 10000 > 0)  # Round up if there's a remainder

# Split the dataframe into batches
for i in range(num_batches):
    start_idx = i * 10000
    end_idx = min((i + 1) * 10000, len(df13))  # Ensure not to exceed the length of the dataframe
    batch_df2 = df13.iloc[start_idx:end_idx]
    
    # Save each batch to a separate file
    filename = f"batch21_{i + 1}.csv"  # Change the file extension if needed
    batch_df2.to_csv(filename, index=False)

    print(f"Saved batch {i + 11} to {filename}")

In [39]:
import pandas as pd

# Assuming df13 is your DataFrame
df13 = df_test2.copy()

# Define the fraction of data to be included in the first split
fraction = 0.5  # Adjust this value as needed

# Create the first DataFrame by sampling a fraction of the original DataFrame
df1 = df13.sample(frac=fraction, random_state=1)

# Create the second DataFrame by dropping the rows in the first DataFrame from the original DataFrame
df2 = df13.drop(df1.index)

# Display the shapes of the resulting DataFrames to verify the split
# print("Shape of original DataFrame:", df13.shape)
# print("Shape of first DataFrame:", df1.shape)
# print("Shape of second DataFrame:", df2.shape)


In [40]:
df8 = pd.concat([df1,df2], axis=0)
df8.shape

(20132, 58)

In [36]:
# df1=df_test2
# df1.columns

Index(['Unnamed: 0.5', 'Unnamed: 0.4', 'Unnamed: 0.3', 'Unnamed: 0.2',
       'Unnamed: 0', 'textid', 'Date', 'Views', 'sourcetype', 'alltext',
       'Text_emt', 'Text_emj', 'Text_langue', 'Text_translate', 'Text_langue2',
       'Text_lower', 'Text_punct', 'Text_tags', 'Text_chat', 'Text_spell',
       'Text_langue3', 'Text_translate2', 'Text_token', 'Text_stop',
       'Text_stem', 'Text_lemma', 'berttopic2', 'cluster_id2',
       'llama2_labelone10', 'cluster_labelone10', 'cluster_id',
       'llama2_labelone', 'cluster_labelone', 'Unnamed: 0.1', 'Text_lemma2',
       'Bertscore_Labels', 'Final_Labels', 'Predicted_Categories3', 'polarity',
       'subjectivity', 'Textblob', 'VADER', 'neg', 'neu', 'pos', 'compound',
       'BERT', 'Sentiment_Score', 'Sentiwordnet', 'llama3_sentiment',
       'Emotion', 'Emotional_Polarity', 'Common_Sentiment32',
       'Predicted_Labels', 'Sentiment2', 'Sentiment2_prediction',
       'Predicted_Labels_roberta', 'Sentiment2_roberta'],
      dtype='ob

In [ ]:
df1.shape

In [ ]:
# # y_pred
# Select relevant columns from df
X_test = df1[['Text_translate2', 'Common_Sentiment32']]

# Apply generate_test_prompt function
X_test = pd.DataFrame(X_test.apply(generate_test_prompt, axis=1), columns=["Text_translate2"])

# Generate predictions for the test set
# y_pred = predict(X_test, model, tokenizer)

# Call the predict function with all required arguments
# y_pred = predict(X_test, model, tokenizer, generator, device)
y_pred = predict(X_test, model, tokenizer, generator, device)#max_input_length)

# Extract true labels from df
y_true = df1['Common_Sentiment32']
# Add predicted values as a new column in the DataFrame
df1['Predicted_Sentiment_finetunned'] = y_pred

/home/hsibitenda/anaconda3/envs/harriet_env/lib/python3.11/site-packages/transformers/pipelines/base.py:1101: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Both `max_new_tokens` (=500) and `max_length`(=128) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Both `max_new_tokens` (=500) and `max_length`(=128) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Both `max_new_tokens` (=500) and

In [ ]:
df1.to_csv('/home/hsibitenda/scratch/harriet/sentiments/batch212_1new22.csv')

In [2]:
# df1.groupby('Predicted_Sentiment_finetunned')['Text_translate2'].count()
df1=pd.read_csv('/home/hsibitenda/scratch/harriet/sentiments/batch212_1new2.csv')
df1=df1.astype(str)

In [44]:
df1.groupby('Predicted_Sentiment_finetunned')['Text_translate2'].count()

Predicted_Sentiment_finetunned
negative    1354
neutral     8388
positive     324
Name: Text_translate2, dtype: int64

In [5]:
df1.groupby('Predicted_Sentiment_finetunned')['Text_translate2'].count()

Predicted_Sentiment_finetunned
negative    4677
neutral      324
positive    5065
Name: Text_translate2, dtype: int64

In [45]:
df2.shape

(10066, 58)

In [ ]:
# # y_pred
# Select relevant columns from df
X_test = df2[['Text_translate2', 'Common_Sentiment32']]

# Apply generate_test_prompt function
X_test = pd.DataFrame(X_test.apply(generate_test_prompt, axis=1), columns=["Text_translate2"])

# Generate predictions for the test set
# y_pred = predict(X_test, model, tokenizer)

# Call the predict function with all required arguments
# y_pred = predict(X_test, model, tokenizer, generator, device)
y_pred = predict(X_test, model, tokenizer, generator, device)#max_input_length)

# Extract true labels from df
y_true = df2['Common_Sentiment32']
# Add predicted values as a new column in the DataFrame
df2['Predicted_Sentiment_finetunned'] = y_pred

/home/hsibitenda/anaconda3/envs/harriet_env/lib/python3.11/site-packages/transformers/pipelines/base.py:1101: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Both `max_new_tokens` (=500) and `max_length`(=128) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Both `max_new_tokens` (=500) and `max_length`(=128) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Both `max_new_tokens` (=500) and

In [ ]:
# df2.columns
df2.to_csv('/home/hsibitenda/scratch/harriet/sentiments/batch212_2new222.csv')

In [2]:
# df1['Sentiment2_prediction']
df2=pd.read_csv('/home/hsibitenda/scratch/harriet/sentiments/batch212_2new22.csv')
df2=df2.astype(str)
df2.shape

(10066, 60)

In [4]:
df1=pd.read_csv('/home/hsibitenda/scratch/harriet/sentiments/batch212_1new2.csv')
df1=df1.astype(str)
df1.shape

(10066, 60)

In [7]:
# df1.columns

In [12]:
# df2.columns
df3=pd.read_csv('/home/hsibitenda/scratch/harriet/sentiment_training2.csv')
df3=df3.astype(str)
df3.shape

(1904, 58)

In [20]:
# df2.columns
df21=df2[['textid', 'Date', 'Views', 'sourcetype', 'alltext',
       'Text_emt', 'Text_emj', 'Text_langue', 'Text_translate', 'Text_langue2',
       'Text_lower', 'Text_punct', 'Text_tags', 'Text_chat', 'Text_spell',
       'Text_langue3', 'Text_translate2', 'Text_token', 'Text_stop',
       'Text_stem', 'Text_lemma', 'berttopic2', 'cluster_id2',
       'llama2_labelone10', 'cluster_labelone10', 'cluster_id',
       'llama2_labelone', 'cluster_labelone', 'Unnamed: 0.1', 'Text_lemma2',
       'Bertscore_Labels', 'Final_Labels', 'Predicted_Categories3', 'polarity',
       'subjectivity', 'Textblob', 'VADER', 'neg', 'neu', 'pos', 'compound',
       'BERT', 'Sentiment_Score', 'Sentiwordnet', 'llama3_sentiment',
       'Emotion', 'Emotional_Polarity', 'Common_Sentiment32', 'Sentiment2',
       'Predicted_Labels', 'Sentiment2_prediction', 'Sentiment2_roberta',
       'Predicted_Labels_roberta','Predicted_Sentiment_finetunned']]
df21.shape

(10066, 54)

In [19]:
# df1.columns
df11=df1[['textid', 'Date', 'Views', 'sourcetype', 'alltext',
       'Text_emt', 'Text_emj', 'Text_langue', 'Text_translate', 'Text_langue2',
       'Text_lower', 'Text_punct', 'Text_tags', 'Text_chat', 'Text_spell',
       'Text_langue3', 'Text_translate2', 'Text_token', 'Text_stop',
       'Text_stem', 'Text_lemma', 'berttopic2', 'cluster_id2',
       'llama2_labelone10', 'cluster_labelone10', 'cluster_id',
       'llama2_labelone', 'cluster_labelone', 'Unnamed: 0.1', 'Text_lemma2',
       'Bertscore_Labels', 'Final_Labels', 'Predicted_Categories3', 'polarity',
       'subjectivity', 'Textblob', 'VADER', 'neg', 'neu', 'pos', 'compound',
       'BERT', 'Sentiment_Score', 'Sentiwordnet', 'llama3_sentiment',
       'Emotion', 'Emotional_Polarity', 'Common_Sentiment32', 'Sentiment2',
       'Predicted_Labels', 'Sentiment2_prediction', 'Sentiment2_roberta',
       'Predicted_Labels_roberta','Predicted_Sentiment_finetunned']]
df11.shape

(10066, 54)

In [18]:
df3['Predicted_Sentiment_finetunned']= df3[['Common_Sentiment32']]
df31=df3[['textid', 'Date', 'Views', 'sourcetype', 'alltext',
       'Text_emt', 'Text_emj', 'Text_langue', 'Text_translate', 'Text_langue2',
       'Text_lower', 'Text_punct', 'Text_tags', 'Text_chat', 'Text_spell',
       'Text_langue3', 'Text_translate2', 'Text_token', 'Text_stop',
       'Text_stem', 'Text_lemma', 'berttopic2', 'cluster_id2',
       'llama2_labelone10', 'cluster_labelone10', 'cluster_id',
       'llama2_labelone', 'cluster_labelone', 'Unnamed: 0.1', 'Text_lemma2',
       'Bertscore_Labels', 'Final_Labels', 'Predicted_Categories3', 'polarity',
       'subjectivity', 'Textblob', 'VADER', 'neg', 'neu', 'pos', 'compound',
       'BERT', 'Sentiment_Score', 'Sentiwordnet', 'llama3_sentiment',
       'Emotion', 'Emotional_Polarity', 'Common_Sentiment32', 'Sentiment2',
       'Predicted_Labels', 'Sentiment2_prediction', 'Sentiment2_roberta',
       'Predicted_Labels_roberta','Predicted_Sentiment_finetunned']]
df31.shape

(1904, 54)

In [21]:
df=pd.concat([df31,df11,df21], axis=0)
df.shape

(22036, 54)

In [22]:
df.columns

Index(['textid', 'Date', 'Views', 'sourcetype', 'alltext', 'Text_emt',
       'Text_emj', 'Text_langue', 'Text_translate', 'Text_langue2',
       'Text_lower', 'Text_punct', 'Text_tags', 'Text_chat', 'Text_spell',
       'Text_langue3', 'Text_translate2', 'Text_token', 'Text_stop',
       'Text_stem', 'Text_lemma', 'berttopic2', 'cluster_id2',
       'llama2_labelone10', 'cluster_labelone10', 'cluster_id',
       'llama2_labelone', 'cluster_labelone', 'Unnamed: 0.1', 'Text_lemma2',
       'Bertscore_Labels', 'Final_Labels', 'Predicted_Categories3', 'polarity',
       'subjectivity', 'Textblob', 'VADER', 'neg', 'neu', 'pos', 'compound',
       'BERT', 'Sentiment_Score', 'Sentiwordnet', 'llama3_sentiment',
       'Emotion', 'Emotional_Polarity', 'Common_Sentiment32', 'Sentiment2',
       'Predicted_Labels', 'Sentiment2_prediction', 'Sentiment2_roberta',
       'Predicted_Labels_roberta', 'Predicted_Sentiment_finetunned'],
      dtype='object')

In [23]:
df.to_csv('/home/hsibitenda/scratch/harriet/sentiment_sentall_llama3.csv')


In [42]:
df2

Unnamed: 0.5 Unnamed: 0.4 Unnamed: 0.3 Unnamed: 0.2 Unnamed: 0 textid  \
1                1            1            1            1          1   4717   
2                2            2            2            2          2  16088   
3                3            3            3            3          3  10340   
9                9            9            9            9          9   8082   
10              11           11           11           11         11  10003   
...            ...          ...          ...          ...        ...    ...   
20121        22025        22025        22025        22025      22025  21501   
20125        22029        22029        22029        22029      22029  18810   
20128        22032        22032        22032        22032      22032  13319   
20130        22034        22034        22034        22034      22034  19270   
20131        22035        22035        22035        22035      22035  21017   

                            Date  Views sourcetype  \
1      2021-11-17 16:39:01+00:00      2    twitter   
2                     2022-08-24     92    youtube   
3            2022-09-16 00:00:00   9600   facebook   
9      2022-08-24 06:24:51+00:00      5    twitter   
10           2022-12-16 00:00:00  27000   facebook   
...                          ...    ...        ...   
20121                 2021-08-24    357    youtube   
20125                 2021-08-24    466    youtube   
20128                 2021-08-24    431    youtube   
20130                 2021-08-24    468    youtube   
20131                 2021-08-24    344    youtube   

                                                 alltext  ...  \
1      blinken is actually on a social vist to b. hus...  ...   
2        social media has improved human communicatio...  ...   
3       nfp leader prof biman prasad - media conferen...  ...   
9      #delocalisedmeeting: west africa is faced with...  ...   
10      blinken echoes ‘concerns’ about russia’s wagn...  ...   
...                                                  ...  ...   
20121    afghanistan: why the taliban can't be defeat...  ...   
20125    afghanistan: why the taliban can't be defeat...  ...   
20128    afghanistan: why the taliban can't be defeat...  ...   
20130    afghanistan: why the taliban can't be defeat...  ...   
20131    afghanistan: why the taliban can't be defeat...  ...   

      llama3_sentiment   Emotion Emotional_Polarity Common_Sentiment32  \
1              neutral  negative           negative           conflict   
2             positive  negative           negative           conflict   
3              neutral  negative           negative           conflict   
9              neutral  positive           positive           conflict   
10             neutral  positive           positive           conflict   
...                ...       ...                ...                ...   
20121          neutral  negative           negative           conflict   
20125          neutral  negative           negative           conflict   
20128          neutral  negative           negative           conflict   
20130          neutral  negative           negative           conflict   
20131          neutral  negative           negative           conflict   

      Predicted_Labels Sentiment2 Sentiment2_prediction  \
1                    0          0              negative   
2                    2          2              positive   
3                    2          2              positive   
9                    2          2              positive   
10                   2          0              positive   
...                ...        ...                   ...   
20121                2          0              positive   
20125                2          0              positive   
20128                2          0              positive   
20130                2          0              positive   
20131                2          0              positive   

      Predicted_Labels_robert

In [43]:
df2.shape

(10066, 59)

In [45]:
df2.columns

Index(['Unnamed: 0.5', 'Unnamed: 0.4', 'Unnamed: 0.3', 'Unnamed: 0.2',
       'Unnamed: 0', 'textid', 'Date', 'Views', 'sourcetype', 'alltext',
       'Text_emt', 'Text_emj', 'Text_langue', 'Text_translate', 'Text_langue2',
       'Text_lower', 'Text_punct', 'Text_tags', 'Text_chat', 'Text_spell',
       'Text_langue3', 'Text_translate2', 'Text_token', 'Text_stop',
       'Text_stem', 'Text_lemma', 'berttopic2', 'cluster_id2',
       'llama2_labelone10', 'cluster_labelone10', 'cluster_id',
       'llama2_labelone', 'cluster_labelone', 'Unnamed: 0.1', 'Text_lemma2',
       'Bertscore_Labels', 'Final_Labels', 'Predicted_Categories3', 'polarity',
       'subjectivity', 'Textblob', 'VADER', 'neg', 'neu', 'pos', 'compound',
       'BERT', 'Sentiment_Score', 'Sentiwordnet', 'llama3_sentiment',
       'Emotion', 'Emotional_Polarity', 'Common_Sentiment32',
       'Predicted_Labels', 'Sentiment2', 'Sentiment2_prediction',
       'Predicted_Labels_roberta', 'Sentiment2_roberta',
       'Predicte

In [44]:
df_test2.shape

(20132, 58)

In [49]:
# df7.to_csv('/home/hsibitenda/scratch/harriet/sentiments_llama2_sentall2.csv')